In [1]:
import numpy as np
import pandas as pd

pd.options.display.max_columns = 100

In [2]:

df_crop_details = pd.read_excel('./data/2.xlsx', sheet_name=1)

In [3]:
# 去除空格
df_crop_details['cropName'] = df_crop_details['cropName'].apply(lambda x: x.strip())
# CropType = [x.strip() for x in CropType]


In [4]:
df_crop_planting = pd.read_excel('./data/2.xlsx', sheet_name=0)
# 照例去除一下空格
df_crop_planting['cropName'] = df_crop_planting['cropName'].apply(lambda x: x.strip())
# ffill
df_crop_planting['landName'] = df_crop_planting['landName'].ffill()
# df_crop_planting

In [5]:
df_land = pd.read_excel('./data/1.xlsx', sheet_name=0)
# 去除landType和landName的空格
df_land['landType'] = df_land['landType'].apply(lambda x: x.strip())
df_land['landName'] = df_land['landName'].apply(lambda x: x.strip())
# df_land

In [6]:

unit_profit_lsc = []
for line in df_crop_details.values:
    s = str(line[7]).split('-')
    unit_profit_lsc.append((float(s[0]) + float(s[1])) / 2 * line[5] - line[6])
df_crop_details['unitProfit'] = unit_profit_lsc
# df_crop_details

In [7]:
df_crop_type_land = pd.read_excel('./data/1.xlsx', sheet_name=1)
# 老规矩，去掉cropName和cropType的空格
df_crop_type_land['cropType'] = df_crop_type_land['cropType'].apply(lambda x: x.strip())
df_crop_type_land['cropName'] = df_crop_type_land['cropName'].apply(lambda x: x.strip())
# df_crop_type_land

In [8]:
# 搞一下季节和年份的集合
SeasonType = ["单季", "第一季", "第二季"]
SeasonDict = {"单季": 1, "第一季": 1, "第二季": 2}
SeasonNum = [1, 2]
years = [2024, 2025, 2026, 2027, 2028, 2029, 2030]

In [9]:
# 枚举地块类型
LandType = {"A": "平旱地", "B": "梯田", "C": "山坡地", "D": "水浇地", "E": "普通大棚", "F": "智慧大棚"}
# LandType

In [10]:
# 枚举地块
LandName = df_crop_planting['landName'].unique()
# LandName

In [11]:
# 枚举地块面积，取df_land的landName为key，landArea为value
LandArea = {x: df_land[df_land['landName'] == x]['landArea'].values[0] for x in LandName}
# LandArea

In [12]:
# 读入作物名称
CropName = df_crop_details['cropName'].unique()
# CropName

In [13]:
# 作物分类
CropType = {x: df_crop_type_land[df_crop_type_land['cropType'] == x]['cropName'].values for x in
            df_crop_type_land['cropType'].values}
CropType['粮食（除了水稻）'] = CropType['粮食'][:-1]  # 这样不太好，但能用
CropType['豆类'] = np.array(list(CropType['粮食（豆类）']) + list(CropType['蔬菜（豆类）']), dtype=object)
CropType

{'粮食（豆类）': array(['黄豆', '黑豆', '红豆', '绿豆', '爬豆'], dtype=object),
 '粮食': array(['小麦', '玉米', '谷子', '高粱', '黍子', '荞麦', '南瓜', '红薯', '莜麦', '大麦', '水稻'],
       dtype=object),
 '蔬菜（豆类）': array(['豇豆', '刀豆', '芸豆'], dtype=object),
 '蔬菜': array(['土豆', '西红柿', '茄子', '菠菜', '青椒', '菜花', '包菜', '油麦菜', '小青菜', '黄瓜',
        '生菜', '辣椒', '空心菜', '黄心菜', '芹菜', '大白菜', '白萝卜', '红萝卜'], dtype=object),
 '食用菌': array(['榆黄菇', '香菇', '白灵菇', '羊肚菌'], dtype=object),
 '粮食（除了水稻）': array(['小麦', '玉米', '谷子', '高粱', '黍子', '荞麦', '南瓜', '红薯', '莜麦', '大麦'],
       dtype=object),
 '豆类': array(['黄豆', '黑豆', '红豆', '绿豆', '爬豆', '豇豆', '刀豆', '芸豆'], dtype=object)}

In [14]:
# any([x[-1] == ' ' for x in CropName])
# 居然有空格
# 现在去掉了

In [15]:
# 亩产量
unit_yield_lsc = {
    l: {
        s: {
            c: df_crop_details[
                (df_crop_details['cropName'] == c) &
                (df_crop_details['cropLandType'] == l) &
                (df_crop_details['season'] == s)
                ]['unitYield'].values[0] if df_crop_details[
                                                (df_crop_details['cropName'] == c) &
                                                (df_crop_details['cropLandType'] == l) &
                                                (df_crop_details['season'] == s)
                                                ]['unitYield'].values.size > 0 else 0
            for c in CropName
        } for s in SeasonType
    }
    for l in LandType.values()
}

# unit_yield

In [16]:
# 亩利润
unit_profit_lsc = {
    l: {
        s: {
            c: df_crop_details[
                (df_crop_details['cropName'] == c) &
                (df_crop_details['cropLandType'] == l) &
                (df_crop_details['season'] == s)
                ]['unitProfit'].values[0]
            if df_crop_details[
                   (df_crop_details['cropName'] == c) &
                   (df_crop_details['cropLandType'] == l) &
                   (df_crop_details['season'] == s)
                   ]['unitYield'].values.size > 0 else 0
            for c in CropName
        } for s in SeasonType
    }
    for l in LandType.values()
}

# unit_profit

In [17]:
# 每种作物的总需求
crop_demand = {
    c: 0
    for c in CropName
}

# 这里需要另一张表
# 代码独立出来移到上面去了

for line in df_crop_planting.values:
    # 面积*该土地类型的亩产量    面积                      地块类型字典 地块类型     季节     作物名称
    crop_demand[line[2]] += line[4] * unit_yield_lsc[LandType[line[0][0]]][line[5]][line[2]]

# crop_demand

In [18]:
# 准备开搞
from pulp import LpMaximize, LpProblem, LpVariable, lpSum, value, LpInteger, PULP_CBC_CMD, LpContinuous, LpBinary
import pulp

In [19]:
model = LpProblem("Crop_Planting_Optimization_with_Specific_Rules", LpMaximize)

In [20]:
# %timeit X = LpVariable.dicts("X", (CropName, LandName, years, seasons), lowBound=0, cat=LpContinuous)
# %timeit XX = LpVariable.dicts("X", [(c, l, y, s) for c in CropName for l in LandName for y in years for s in seasons],lowBound=0, cat=LpContinuous)

In [21]:
# 地块l在y年的s季的种植c的量
# X = LpVariable.dicts("crop_plant_area", (CropName, LandName, years, SeasonType), lowBound=0, cat=LpContinuous)
X = LpVariable.dicts("X", [(c, l, y, s)
                           for c in CropName
                           for l in LandName
                           for y in years
                           for s in SeasonType],
                     lowBound=0,
                     cat=LpContinuous
                     )
# X

In [22]:
# 地块l在y年的s季是否种植了c
# Y = LpVariable.dicts("crop_plant_bool", (CropName, LandName, years, SeasonType), cat=LpBinary)
Y = LpVariable.dicts("Y", [(c, l, y, s) for c in CropName for l in LandName for y in years for s in SeasonType],
                     cat=LpBinary)

# Y

In [23]:
# 确保与X进行01约束
for c in CropName:
    for l in LandName:
        for y in years:
            for s in SeasonType:
                # 如果种植了作物，则种植面积大于0
                model += X[c, l, y, s] <= 10000000 * Y[c, l, y, s], f"PlantingConstraint1_{c}_{l}_{y}_{s}"
                # 如果未种植作物，则种植面积为0
                model += X[c, l, y, s] >= 0.000001 * Y[c, l, y, s], f"PlantingConstraint2_{c}_{l}_{y}_{s}"

In [24]:
# 目标函数：总利润 = sum(x[i]*profit[c,l,s])
model += lpSum(  #  地块类型      季节 作物类型
    X[c, l, y, s] * unit_profit_lsc[LandType[l[0]]][s][c]
    for c in CropName
    for l in LandName
    for y in years
    for s in SeasonType
), "total_profit"


In [25]:
# 约束，启动！
# 条件1：每年的所有季节中每种作物的种植量必须小于需求量
for c in CropName:
    for y in years:
        model += lpSum(X[c, l, y, s] * unit_yield_lsc[LandType[l[0]]][s][c] for l in LandName for s in SeasonType) <= \
                 crop_demand[c], f"CropDemandConstraint_{c}_{y}"

In [26]:
# 条件2： 每年每季每块地的种植面积不能超过该地块的总面积
for l in LandName:
    for y in years:
        for s in SeasonType:
            model += lpSum(X[c, l, y, s] for c in CropName) <= LandArea[l], f"LandAreaConstraint_{l}_{y}_{s}"

In [27]:
# 条件3： 平旱地、梯田和山坡地每年适宜单季种植[粮食类作物（水稻除外）]。因为除了[粮食类作物（水稻除外）]以外的作物似乎已经被上面的产量和利润的0给约束了，所以大概不需要做限制了吧
for l in LandName:
    if l[0] not in ["A", "B", "C"]:  # ["平旱地", "梯田", "山坡地"]
        continue
    for s in SeasonType:
        if s != "单季":
            model += lpSum(Y[c, l, y, s] for c in CropName for y in years) == 0, f"SingleSeasonConstraint_{l}_{s}"
            # model += lpSum(X[c, l, y, s] for c in CropName for y in years) == 0

In [28]:
# 条件4： 水浇地每年可以单季种植水稻或两季种植蔬菜作物。
for l in LandName:
    if l[0] != "D":  # ["水浇地"]
        continue
    for y in years:
        model += (
                         (lpSum(Y["水稻", l, y, "单季"]) != 0) and
                         (lpSum(
                             Y[c, l, y, s] if c != "水稻" else 0
                             for c in CropName
                             for s in ["第一季", "第二季"]
                         ) == 0)
                 ) or (
                         (lpSum(Y["水稻", l, y, "单季"]) == 0) and
                         (lpSum(
                             Y[c, l, y, s] if c != "水稻" else 0
                             for c in CropName
                             for s in ["第一季", "第二季"]
                         ) != 0)
                 ), f"irrigatedConstraint_{l}_{y}"



In [29]:
# 条件5： 若在某块水浇地种植两季蔬菜，第一季可种植多种蔬菜（大白菜、白萝卜和红萝卜除外）；第二季只能种植大白菜、白萝卜和红萝卜中的一种（便于管理）。
# 感觉没必要，因为前面有field和profit为0的惩罚


In [30]:
# 条件6： 根据季节性要求，大白菜、白萝卜和红萝卜只能在水浇地的第二季种植。
# 感觉也没必要，同理


In [31]:
# 条件7： 普通大棚每年种植两季作物，第一季可种植多种蔬菜（大白菜、白萝卜和红萝卜除外），第二季只能种植食用菌。
# 同理


In [32]:
# 条件8： 食用菌类只能在普通大棚第二季的时候种植
# 同理


In [33]:
# 条件9： 智慧大棚每年都可种植两季蔬菜（大白菜、白萝卜和红萝卜除外）
# 同理

In [29]:
# 条件10： 别种得太碎了，啥意思？ 每种作物不超过3块地吧。
for c in CropName:
    for y in years:
        for s in SeasonType:
            model += lpSum(Y[c, l, y, s] for l in LandName) <= 3, f"MaxCropTypeConstraint_{c}_{y}_{s}"

In [30]:
# 条件11： 最小种植面积：0.2吧
for l in LandName:
    for y in years:
        for s in SeasonType:
            for c in CropName:
                model += X[c, l, y, s] >= 0.2 * (1 if Y[c, l, y, s] else 0), f"MinCropAreaConstraint_{c}_{l}_{y}_{s}"

In [31]:
# 条件12 ： 最重要的，不能重复种植同一块地同一年同一季的同一作物
# 每种作物在同一地块（含大棚）都不能连续重茬种植

for l in LandName:
    for c in CropName:
        for y in years:  # 单季不能连年种植 同一年不能连续种植 跨年也不能连续种植
            if y < years[-1]:
                model += Y[c, l, y, "单季"] + Y[c, l, y + 1, "单季"] <= 1, f"SingleSeasonConstraint1_{c}_{l}_{y}"
                model += Y[c, l, y, "第一季"] + Y[c, l, y + 1, "第二季"] <= 1, f"DoubleSeasonConstraint1_{c}_{l}_{y}"
            model += Y[c, l, y, "第一季"] + Y[c, l, y, "第二季"] <= 1, f"DoubleSeasonConstraint2_{c}_{l}_{y}"


In [37]:
# 条件13： 最重要的，从 2023 年开始要求每个地块（含大棚） 的所有土地三年内至少种植一次豆类作物
# CropType['豆类']
for l in LandName:
    for y in years[:-2]:
        model += lpSum(Y[c,l,y_r,s] for c in CropType['豆类'] for y_r in range(y,y+2) for s in SeasonType)>=1, f"BeanConstraint_{l}_{y}"
        # model += lpSum(Y[c, l, y_r, "单季"] for c in CropType['豆类'] for y_r in
        #                range(y - 2, y + 1)) >= 1, f"BeanConstraint1_{l}_{y}"
        # model += lpSum(Y[c, l, y_r, s] for c in CropType['豆类'] for y_r in range(y - 2, y + 1) for s in
        #                ["第一季", "第二季"]) >= 1, f"BeanConstraint2_{l}_{y}"

In [32]:
# model.solve()

# 创建求解器实例
solver = pulp.PULP_CBC_CMD(
    timeLimit=120,
    threads=4,
)
solver.solve(model)


# print(Y)
# for c in CropName:
#     for l in LandName:
#         for y in years:
#             for s in SeasonType:
#                 print(f"Y[({c}, {l}, {y}, {s})] = {pulp.value(Y[(c, l, y, s)])}")


1

In [40]:

# 输出文件名，包含起始年份和结束年份
output_filename = f"planting_plan_{years[0]}-{years[-1]}.xlsx"

# 使用 pd.ExcelWriter 创建 Excel 文件
with pd.ExcelWriter(output_filename) as writer:
    # 遍历每一年和每个季节
    for y in years:
        for s in SeasonType:
            # 创建一个空的 DataFrame，横轴为作物名称，纵轴为地块名称
            result_table = pd.DataFrame(columns=CropName, index=LandName)

            # 填充表格数据
            for l in LandName:
                for c in CropName:
                    # 获取变量 X[c, l, y, s] 的值
                    crop_value = value(X[c, l, y, s])
                    if crop_value is not None and crop_value > 0:
                        result_table.at[l, c] = crop_value  # 填入结果

            # 用 0 填充空值
            result_table.fillna(0, inplace=True)

            # 定义每个 sheet 的名称为 年份_季节
            sheet_name = f"{y}_Season_{s}"

            # 将每个 result_table 写入到 Excel 的不同 sheet 中
            result_table.to_excel(writer, sheet_name=sheet_name)

print(f"结果已保存到文件：{output_filename}")


结果已保存到文件：planting_plan_2024-2030.xlsx
